In [1]:
import open3d as o3d
import torch
import numpy as np

import objaverse
import multiprocessing
import trimesh

from ipywidgets import interact, interactive, fixed, interact_manual
import ipywidgets as widgets

Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.
[Open3D INFO] WebRTCWindowSystem: HTTP handshake server disabled.


In [2]:
tesla_uid = '2c91f1d43c174e1493e29b4a0e6229da'
model_annot = objaverse.load_annotations([tesla_uid])

In [3]:
processes = multiprocessing.cpu_count()

In [4]:
objects = objaverse.load_objects(
    uids=[tesla_uid],
    download_processes=processes
)

In [5]:
objects

{'2c91f1d43c174e1493e29b4a0e6229da': '/home/aleks/.objaverse/hf-objaverse-v1/glbs/000-130/2c91f1d43c174e1493e29b4a0e6229da.glb'}

In [6]:
model_scene = trimesh.load(objects[tesla_uid])
model_scene.show()

In [7]:
model_trimesh = trimesh.points.PointCloud(model_scene.dump()[0].vertices)

In [11]:
model_o3d = o3d.geometry.PointCloud()
model_o3d.points = o3d.utility.Vector3dVector(np.asarray(model_trimesh.vertices))
if model_trimesh.colors.size > 0:
    model_o3d.colors = o3d.utility.Vector3dVector(np.asarray(model_trimesh.colors))

In [12]:
model_o3d

PointCloud with 55130 points.

In [13]:
from os import path

dataset_path = '/mnt/3dcv/projects/openscene_test/data/scannet/scannet_3d'
example_path = 'train/scene0000_00_vh_clean_2.pth'
path = path.join(dataset_path, example_path)    

scene_array, scene_colors, scene_annot = torch.load(path)

In [16]:
@interact(filter_by_annot=True, filter_annot=(0,20))
def g(filter_by_annot, filter_annot):
    
    if filter_by_annot:
        indices = (scene_annot == filter_annot)
    else:
        indices = np.full(scene_annot.shape, True)

    scene_o3d = o3d.geometry.PointCloud()
    scene_o3d.points = o3d.utility.Vector3dVector(scene_array[indices])
    scene_o3d.colors = o3d.utility.Vector3dVector(scene_colors[indices])

    o3d.visualization.draw_plotly([scene_o3d], width=900, height=700)

interactive(children=(Checkbox(value=True, description='filter_by_annot'), IntSlider(value=10, description='fi…